## Extra requirements
```bash
pip install -q -U google-genai
```

## Required environment variable
GEMINI_API_KEY

### How to get GEMINI API KEY

Use the link: [gemini api key](https://aistudio.google.com/app/apikey) to get yours.

In [1]:
import os
import requests
from bs4 import BeautifulSoup
from dotenv import load_dotenv
from google import genai
from google.genai import types


In [53]:
load_dotenv()
api_key = os.getenv("GEMINI_API_KEY")

if not api_key or len(api_key) < 39:
    print("No correct api key was found")
else:
    print("Api key found. Good to go!")

Api key found. Good to go!


In [54]:
client = genai.Client(api_key=api_key)

In [55]:
class Website:
    url: str
    title: str
    text: str

    def __init__(self, url):
        self.url = url
        response = requests.get(url)
        soup = BeautifulSoup(response.content, "html.parser")
        self.title = soup.title.string if soup.title else "No title was found"

        for irr in soup.body(["script", "style", "img", "input"]):
            irr.decompose()
        self.text = soup.body.get_text(separator="\n", strip=True)
            
        

In [ ]:
ed = Website("https://edwarddonner.com")
print(ed.title)
print(ed.text)

In [57]:
system_prompt = "You are an assistant that analyzes the contents of a website \
and provides a short summary, ignoring text that navigation related. Respond \
in markdown."

In [58]:
def user_prompt_for(website):
    user_prompt = f"You are looking at a website titled {website.title}"
    user_prompt += "\nThe contents of this website is as follows; \
please provide a short summary of this website in markdown. \
If it includes news or announcements, then summarize these too.\n\n"
    user_prompt += website.text
    return user_prompt

In [61]:
def summarize(url):
    website = Website(url)
    response = client.models.generate_content(
        model="gemini-2.0-flash",
        config=types.GenerateContentConfig(
            system_instruction=system_prompt),
            contents=user_prompt_for(website)
        )
    return response.text

In [62]:
summarize("https://edwarddonner.com")

"Edward Donner's website introduces Ed, a coder and LLM enthusiast who enjoys DJing, electronic music, and Hacker News. He is the co-founder and CTO of Nebula.io, an AI company focused on talent discovery. He was also the founder and CEO of AI startup untapt, which was acquired in 2021. The site also has links to LLM resources from past workshops and posts.\n"

### Output
"Edward Donner's website introduces Ed, a coder and LLM enthusiast who enjoys DJing, electronic music, and Hacker News. He is the co-founder and CTO of Nebula.io, an AI company focused on talent discovery. He was also the founder and CEO of AI startup untapt, which was acquired in 2021. The site also has links to LLM resources from past workshops and posts.\n"
